In [103]:
from pyspark.sql import SparkSession
import pyspark.pandas as ps
import numpy as np
from datetime import datetime, date
import pandas as pd
from pyspark.sql import Row
from pyspark.sql.types import StructType,StructField, StringType,ArrayType,IntegerType
from pyspark.sql.functions import col,lit,sum,avg,max,min,mean,count,udf,concat,broadcast,explode,split,concat_ws,desc,asc,when
from pyspark.context import SparkContext
from pyspark import SparkConf

In [2]:
spark = SparkSession.builder.getOrCreate()

23/06/13 23:07:16 WARN Utils: Your hostname, ajinkyas-MacBook-Pro.local resolves to a loopback address: 127.0.0.1; using 192.168.0.135 instead (on interface en0)
23/06/13 23:07:16 WARN Utils: Set SPARK_LOCAL_IP if you need to bind to another address
Setting default log level to "WARN".
To adjust logging level use sc.setLogLevel(newLevel). For SparkR, use setLogLevel(newLevel).
23/06/13 23:07:18 WARN NativeCodeLoader: Unable to load native-hadoop library for your platform... using builtin-java classes where applicable


In [3]:
schema = StructType([
    StructField("mainBranch",StringType(),True),
     StructField("employment",StringType(),True),
     StructField("remoteWork",StringType(),True),
     StructField("codingActivities",StringType(),True)
])

In [4]:
df = spark.read.format("csv").option("header", "true").schema(schema).load("/Users/ajinkyaparkar/Documents/leetcode/AWS/data/stackOverflow/survey_results_public.csv")



In [5]:
df.show()

23/06/13 23:07:26 WARN CSVHeaderChecker: Number of column in CSV header is not equal to number of fields in the schema:
 Header length: 79, schema size: 4
CSV file: file:///Users/ajinkyaparkar/Documents/leetcode/AWS/data/stackOverflow/survey_results_public.csv


+----------+--------------------+--------------------+--------------------+
|mainBranch|          employment|          remoteWork|    codingActivities|
+----------+--------------------+--------------------+--------------------+
|         1|       None of these|                  NA|                  NA|
|         2|I am a developer ...| Employed, full-time|        Fully remote|
|         3|I am not primaril...| Employed, full-time|Hybrid (some remo...|
|         4|I am a developer ...| Employed, full-time|        Fully remote|
|         5|I am a developer ...| Employed, full-time|Hybrid (some remo...|
|         6|I am not primaril...|  Student, full-time|                  NA|
|         7|I code primarily ...|  Student, part-time|                  NA|
|         8|I am a developer ...|Not employed, but...|                  NA|
|         9|I am a developer ...| Employed, full-time|Hybrid (some remo...|
|        10|I am a developer ...|Independent contr...|        Fully remote|
|        11|

In [6]:
#df = spark.read.option("header", "true").csv("/Users/ajinkyaparkar/Documents/leetcode/AWS/data/stackOverflow/survey_results_public.csv").schema(schema)


In [7]:
#df = df.select("MainBranch","Employment","RemoteWork","CodingActivities")

In [8]:
df.withColumn("mainBranch",(col("mainBranch")*2).cast("Integer")).schema

StructType([StructField('mainBranch', IntegerType(), True), StructField('employment', StringType(), True), StructField('remoteWork', StringType(), True), StructField('codingActivities', StringType(), True)])

In [9]:
df.withColumn("CopiedColumn",concat(col("mainBranch") ,lit(" "), col("remoteWork"))).show(truncate=True)

+----------+--------------------+--------------------+--------------------+--------------------+
|mainBranch|          employment|          remoteWork|    codingActivities|        CopiedColumn|
+----------+--------------------+--------------------+--------------------+--------------------+
|         1|       None of these|                  NA|                  NA|                1 NA|
|         2|I am a developer ...| Employed, full-time|        Fully remote|2 Employed, full-...|
|         3|I am not primaril...| Employed, full-time|Hybrid (some remo...|3 Employed, full-...|
|         4|I am a developer ...| Employed, full-time|        Fully remote|4 Employed, full-...|
|         5|I am a developer ...| Employed, full-time|Hybrid (some remo...|5 Employed, full-...|
|         6|I am not primaril...|  Student, full-time|                  NA|6 Student, full-time|
|         7|I code primarily ...|  Student, part-time|                  NA|7 Student, part-time|
|         8|I am a developer .

23/06/13 23:07:27 WARN CSVHeaderChecker: Number of column in CSV header is not equal to number of fields in the schema:
 Header length: 79, schema size: 4
CSV file: file:///Users/ajinkyaparkar/Documents/leetcode/AWS/data/stackOverflow/survey_results_public.csv


In [10]:
df.withColumn("CopiedColumn",(col("mainBranch")*2).cast("Integer")).show(truncate=True)

+----------+--------------------+--------------------+--------------------+------------+
|mainBranch|          employment|          remoteWork|    codingActivities|CopiedColumn|
+----------+--------------------+--------------------+--------------------+------------+
|         1|       None of these|                  NA|                  NA|           2|
|         2|I am a developer ...| Employed, full-time|        Fully remote|           4|
|         3|I am not primaril...| Employed, full-time|Hybrid (some remo...|           6|
|         4|I am a developer ...| Employed, full-time|        Fully remote|           8|
|         5|I am a developer ...| Employed, full-time|Hybrid (some remo...|          10|
|         6|I am not primaril...|  Student, full-time|                  NA|          12|
|         7|I code primarily ...|  Student, part-time|                  NA|          14|
|         8|I am a developer ...|Not employed, but...|                  NA|          16|
|         9|I am a de

23/06/13 23:07:27 WARN CSVHeaderChecker: Number of column in CSV header is not equal to number of fields in the schema:
 Header length: 79, schema size: 4
CSV file: file:///Users/ajinkyaparkar/Documents/leetcode/AWS/data/stackOverflow/survey_results_public.csv


In [11]:
df.withColumn("Country", lit(None)).show()

+----------+--------------------+--------------------+--------------------+-------+
|mainBranch|          employment|          remoteWork|    codingActivities|Country|
+----------+--------------------+--------------------+--------------------+-------+
|         1|       None of these|                  NA|                  NA|   null|
|         2|I am a developer ...| Employed, full-time|        Fully remote|   null|
|         3|I am not primaril...| Employed, full-time|Hybrid (some remo...|   null|
|         4|I am a developer ...| Employed, full-time|        Fully remote|   null|
|         5|I am a developer ...| Employed, full-time|Hybrid (some remo...|   null|
|         6|I am not primaril...|  Student, full-time|                  NA|   null|
|         7|I code primarily ...|  Student, part-time|                  NA|   null|
|         8|I am a developer ...|Not employed, but...|                  NA|   null|
|         9|I am a developer ...| Employed, full-time|Hybrid (some remo...| 

23/06/13 23:07:27 WARN CSVHeaderChecker: Number of column in CSV header is not equal to number of fields in the schema:
 Header length: 79, schema size: 4
CSV file: file:///Users/ajinkyaparkar/Documents/leetcode/AWS/data/stackOverflow/survey_results_public.csv


In [12]:
df.withColumnRenamed("mainBranch","index").show()

23/06/13 23:07:27 WARN CSVHeaderChecker: Number of column in CSV header is not equal to number of fields in the schema:
 Header length: 79, schema size: 4
CSV file: file:///Users/ajinkyaparkar/Documents/leetcode/AWS/data/stackOverflow/survey_results_public.csv


+-----+--------------------+--------------------+--------------------+
|index|          employment|          remoteWork|    codingActivities|
+-----+--------------------+--------------------+--------------------+
|    1|       None of these|                  NA|                  NA|
|    2|I am a developer ...| Employed, full-time|        Fully remote|
|    3|I am not primaril...| Employed, full-time|Hybrid (some remo...|
|    4|I am a developer ...| Employed, full-time|        Fully remote|
|    5|I am a developer ...| Employed, full-time|Hybrid (some remo...|
|    6|I am not primaril...|  Student, full-time|                  NA|
|    7|I code primarily ...|  Student, part-time|                  NA|
|    8|I am a developer ...|Not employed, but...|                  NA|
|    9|I am a developer ...| Employed, full-time|Hybrid (some remo...|
|   10|I am a developer ...|Independent contr...|        Fully remote|
|   11|I am a developer ...| Employed, full-time|Hybrid (some remo...|
|   12

In [13]:
df.filter(col("employment").like("%I am not%")).show()

+----------+--------------------+--------------------+--------------------+
|mainBranch|          employment|          remoteWork|    codingActivities|
+----------+--------------------+--------------------+--------------------+
|         3|I am not primaril...| Employed, full-time|Hybrid (some remo...|
|         6|I am not primaril...|  Student, full-time|                  NA|
|        12|I am not primaril...|Employed, full-ti...|        Fully remote|
|        24|I am not primaril...| Employed, full-time|Hybrid (some remo...|
|        34|I am not primaril...|Student, part-tim...|      Full in-person|
|        36|I am not primaril...|  Student, full-time|                  NA|
|        51|I am not primaril...|Employed, full-ti...|      Full in-person|
|        84|I am not primaril...| Employed, full-time|        Fully remote|
|        91|I am not primaril...| Employed, full-time|        Fully remote|
|       124|I am not primaril...| Employed, full-time|      Full in-person|
|       155|

23/06/13 23:07:28 WARN CSVHeaderChecker: Number of column in CSV header is not equal to number of fields in the schema:
 Header length: 79, schema size: 4
CSV file: file:///Users/ajinkyaparkar/Documents/leetcode/AWS/data/stackOverflow/survey_results_public.csv


In [14]:
df.filter(col("mainBranch").between(0,5)).show()

23/06/13 23:07:28 WARN CSVHeaderChecker: Number of column in CSV header is not equal to number of fields in the schema:
 Header length: 79, schema size: 4
CSV file: file:///Users/ajinkyaparkar/Documents/leetcode/AWS/data/stackOverflow/survey_results_public.csv


+----------+--------------------+-------------------+--------------------+
|mainBranch|          employment|         remoteWork|    codingActivities|
+----------+--------------------+-------------------+--------------------+
|         1|       None of these|                 NA|                  NA|
|         2|I am a developer ...|Employed, full-time|        Fully remote|
|         3|I am not primaril...|Employed, full-time|Hybrid (some remo...|
|         4|I am a developer ...|Employed, full-time|        Fully remote|
|         5|I am a developer ...|Employed, full-time|Hybrid (some remo...|
+----------+--------------------+-------------------+--------------------+



In [15]:
df.filter(col("employment").contains("not")).show()

+----------+--------------------+--------------------+--------------------+
|mainBranch|          employment|          remoteWork|    codingActivities|
+----------+--------------------+--------------------+--------------------+
|         3|I am not primaril...| Employed, full-time|Hybrid (some remo...|
|         6|I am not primaril...|  Student, full-time|                  NA|
|        12|I am not primaril...|Employed, full-ti...|        Fully remote|
|        24|I am not primaril...| Employed, full-time|Hybrid (some remo...|
|        34|I am not primaril...|Student, part-tim...|      Full in-person|
|        36|I am not primaril...|  Student, full-time|                  NA|
|        51|I am not primaril...|Employed, full-ti...|      Full in-person|
|        84|I am not primaril...| Employed, full-time|        Fully remote|
|        91|I am not primaril...| Employed, full-time|        Fully remote|
|       124|I am not primaril...| Employed, full-time|      Full in-person|
|       155|

23/06/13 23:07:30 WARN CSVHeaderChecker: Number of column in CSV header is not equal to number of fields in the schema:
 Header length: 79, schema size: 4
CSV file: file:///Users/ajinkyaparkar/Documents/leetcode/AWS/data/stackOverflow/survey_results_public.csv


In [16]:
df.select(df.columns[:2]).show(truncate=False)

+----------+-----------------------------------------------------------------------------+
|mainBranch|employment                                                                   |
+----------+-----------------------------------------------------------------------------+
|1         |None of these                                                                |
|2         |I am a developer by profession                                               |
|3         |I am not primarily a developer, but I write code sometimes as part of my work|
|4         |I am a developer by profession                                               |
|5         |I am a developer by profession                                               |
|6         |I am not primarily a developer, but I write code sometimes as part of my work|
|7         |I code primarily as a hobby                                                  |
|8         |I am a developer by profession                                               |

23/06/13 23:07:30 WARN CSVHeaderChecker: CSV header does not conform to the schema.
 Header: ResponseId, MainBranch
 Schema: mainBranch, employment
Expected: mainBranch but found: ResponseId
CSV file: file:///Users/ajinkyaparkar/Documents/leetcode/AWS/data/stackOverflow/survey_results_public.csv


In [17]:
df.select(col("employment").cast("string")).show()

+--------------------+
|          employment|
+--------------------+
|       None of these|
|I am a developer ...|
|I am not primaril...|
|I am a developer ...|
|I am a developer ...|
|I am not primaril...|
|I code primarily ...|
|I am a developer ...|
|I am a developer ...|
|I am a developer ...|
|I am a developer ...|
|I am not primaril...|
|I am a developer ...|
|I am a developer ...|
|I am a developer ...|
|I am a developer ...|
|I am a developer ...|
|I am a developer ...|
|I am a developer ...|
|I am learning to ...|
+--------------------+
only showing top 20 rows



23/06/13 23:07:30 WARN CSVHeaderChecker: CSV header does not conform to the schema.
 Header: MainBranch
 Schema: employment
Expected: employment but found: MainBranch
CSV file: file:///Users/ajinkyaparkar/Documents/leetcode/AWS/data/stackOverflow/survey_results_public.csv


In [18]:
df.distinct().count()

23/06/13 23:07:31 WARN CSVHeaderChecker: Number of column in CSV header is not equal to number of fields in the schema:
 Header length: 79, schema size: 4
CSV file: file:///Users/ajinkyaparkar/Documents/leetcode/AWS/data/stackOverflow/survey_results_public.csv


73268

In [19]:
df.dropDuplicates().show()

23/06/13 23:07:33 WARN CSVHeaderChecker: Number of column in CSV header is not equal to number of fields in the schema:
 Header length: 79, schema size: 4
CSV file: file:///Users/ajinkyaparkar/Documents/leetcode/AWS/data/stackOverflow/survey_results_public.csv


+----------+--------------------+--------------------+--------------------+
|mainBranch|          employment|          remoteWork|    codingActivities|
+----------+--------------------+--------------------+--------------------+
|        75|I am a developer ...| Employed, full-time|      Full in-person|
|       110|I am a developer ...| Employed, full-time|        Fully remote|
|       256|I am a developer ...| Employed, full-time|      Full in-person|
|       296|I am a developer ...|Not employed, but...|                  NA|
|       634|I am a developer ...| Employed, full-time|Hybrid (some remo...|
|       843|I am a developer ...| Employed, full-time|        Fully remote|
|       884|I am a developer ...| Employed, full-time|        Fully remote|
|      1193|I am a developer ...| Employed, full-time|        Fully remote|
|      1277|I am a developer ...| Employed, full-time|        Fully remote|
|      1415|I am a developer ...| Employed, full-time|        Fully remote|
|      1517|

In [20]:
df.sort(col("employment").desc()).show()

23/06/13 23:07:34 WARN CSVHeaderChecker: Number of column in CSV header is not equal to number of fields in the schema:
 Header length: 79, schema size: 4
CSV file: file:///Users/ajinkyaparkar/Documents/leetcode/AWS/data/stackOverflow/survey_results_public.csv


+----------+-------------+----------+----------------+
|mainBranch|   employment|remoteWork|codingActivities|
+----------+-------------+----------+----------------+
|     66937|None of these|        NA|              NA|
|     57242|None of these|        NA|              NA|
|     11077|None of these|        NA|              NA|
|     58061|None of these|        NA|              NA|
|     48544|None of these|        NA|              NA|
|     57243|None of these|        NA|              NA|
|     12773|None of these|        NA|              NA|
|     57228|None of these|        NA|              NA|
|      1507|None of these|        NA|              NA|
|     57257|None of these|        NA|              NA|
|     11206|None of these|        NA|              NA|
|     56732|None of these|        NA|              NA|
|     50715|None of these|        NA|              NA|
|     57259|None of these|        NA|              NA|
|     10873|None of these|        NA|              NA|
|     5683

In [21]:
df.createOrReplaceTempView("EMP")
spark.sql("select employment,count(employment) as count from EMP group by employment order by count desc").show()

23/06/13 23:07:35 WARN CSVHeaderChecker: CSV header does not conform to the schema.
 Header: MainBranch
 Schema: employment
Expected: employment but found: MainBranch
CSV file: file:///Users/ajinkyaparkar/Documents/leetcode/AWS/data/stackOverflow/survey_results_public.csv


+--------------------+-----+
|          employment|count|
+--------------------+-----+
|I am a developer ...|53507|
|I am learning to ...| 6309|
|I am not primaril...| 5794|
|I code primarily ...| 4865|
|       None of these| 1497|
|I used to be a de...| 1296|
+--------------------+-----+



In [22]:
df.schema

StructType([StructField('mainBranch', StringType(), True), StructField('employment', StringType(), True), StructField('remoteWork', StringType(), True), StructField('codingActivities', StringType(), True)])

In [23]:
df.withColumn("mainBranch",col("mainBranch").cast("Integer")).groupBy(col("employment")).min("mainBranch").alias("min").show()


23/06/13 23:07:36 WARN CSVHeaderChecker: CSV header does not conform to the schema.
 Header: ResponseId, MainBranch
 Schema: mainBranch, employment
Expected: mainBranch but found: ResponseId
CSV file: file:///Users/ajinkyaparkar/Documents/leetcode/AWS/data/stackOverflow/survey_results_public.csv


+--------------------+---------------+
|          employment|min(mainBranch)|
+--------------------+---------------+
|I am not primaril...|              3|
|I code primarily ...|              7|
|I am a developer ...|              2|
|I used to be a de...|             73|
|I am learning to ...|             20|
|       None of these|              1|
+--------------------+---------------+



In [24]:
df.withColumn("mainBranch",col("mainBranch").cast("Integer"))\
.groupBy(col("employment")).agg(sum(col("mainBranch")).alias("Summation"),\
                                avg(col("mainBranch")).cast("Integer").alias("Average")).where(col("Summation")>252522203).show()



23/06/13 23:07:37 WARN CSVHeaderChecker: CSV header does not conform to the schema.
 Header: ResponseId, MainBranch
 Schema: mainBranch, employment
Expected: mainBranch but found: ResponseId
CSV file: file:///Users/ajinkyaparkar/Documents/leetcode/AWS/data/stackOverflow/survey_results_public.csv


+--------------------+----------+-------+
|          employment| Summation|Average|
+--------------------+----------+-------+
|I am a developer ...|1920149008|  35885|
+--------------------+----------+-------+



In [25]:
df2 =  spark.read.format("csv").option("header", "true").schema(schema).load("/Users/ajinkyaparkar/Documents/leetcode/AWS/data/stackOverflow/survey_results_public.csv")



In [26]:
df.join(df2,df.mainBranch == df2.mainBranch,"inner").show()

23/06/13 23:07:38 WARN CSVHeaderChecker: Number of column in CSV header is not equal to number of fields in the schema:
 Header length: 79, schema size: 4
CSV file: file:///Users/ajinkyaparkar/Documents/leetcode/AWS/data/stackOverflow/survey_results_public.csv


+----------+--------------------+--------------------+--------------------+----------+--------------------+--------------------+--------------------+
|mainBranch|          employment|          remoteWork|    codingActivities|mainBranch|          employment|          remoteWork|    codingActivities|
+----------+--------------------+--------------------+--------------------+----------+--------------------+--------------------+--------------------+
|       296|I am a developer ...|Not employed, but...|                  NA|       296|I am a developer ...|Not employed, but...|                  NA|
|       467|I am a developer ...| Employed, full-time|Hybrid (some remo...|       467|I am a developer ...| Employed, full-time|Hybrid (some remo...|
|       675|I am a developer ...| Employed, full-time|Hybrid (some remo...|       675|I am a developer ...| Employed, full-time|Hybrid (some remo...|
|       691|I am learning to ...|Not employed, and...|                  NA|       691|I am learning 

In [27]:
df3 = df.union(df2)

In [28]:
df.count()

73268

In [29]:
df3.count()

146536

In [30]:
df3.distinct().count()

23/06/13 23:07:40 WARN CSVHeaderChecker: Number of column in CSV header is not equal to number of fields in the schema:
 Header length: 79, schema size: 4
CSV file: file:///Users/ajinkyaparkar/Documents/leetcode/AWS/data/stackOverflow/survey_results_public.csv


73268

In [31]:
df3 = df.unionByName(df2)

In [32]:
df3.printSchema

<bound method DataFrame.printSchema of DataFrame[mainBranch: string, employment: string, remoteWork: string, codingActivities: string]>

In [33]:
def convertCase(str):
    resStr=""
    arr = str.split(" ")
    for x in arr:
       resStr= resStr + x[0:1].lower() + x[1:len(x)] + " "
    return resStr 

In [34]:
convertUDF = udf(lambda x:convertCase(x),StringType())

In [35]:
df.columns

['mainBranch', 'employment', 'remoteWork', 'codingActivities']

In [36]:
df.select(col("employment"),convertUDF(col("employment")).alias("employment")).show()

+--------------------+--------------------+
|          employment|          employment|
+--------------------+--------------------+
|       None of these|      none of these |
|I am a developer ...|i am a developer ...|
|I am not primaril...|i am not primaril...|
|I am a developer ...|i am a developer ...|
|I am a developer ...|i am a developer ...|
|I am not primaril...|i am not primaril...|
|I code primarily ...|i code primarily ...|
|I am a developer ...|i am a developer ...|
|I am a developer ...|i am a developer ...|
|I am a developer ...|i am a developer ...|
|I am a developer ...|i am a developer ...|
|I am not primaril...|i am not primaril...|
|I am a developer ...|i am a developer ...|
|I am a developer ...|i am a developer ...|
|I am a developer ...|i am a developer ...|
|I am a developer ...|i am a developer ...|
|I am a developer ...|i am a developer ...|
|I am a developer ...|i am a developer ...|
|I am a developer ...|i am a developer ...|
|I am learning to ...|i am learn

23/06/13 23:07:42 WARN CSVHeaderChecker: CSV header does not conform to the schema.
 Header: MainBranch
 Schema: employment
Expected: employment but found: MainBranch
CSV file: file:///Users/ajinkyaparkar/Documents/leetcode/AWS/data/stackOverflow/survey_results_public.csv


In [37]:
spark.udf.register("convertUDF", convertCase,StringType())

<function __main__.convertCase(str)>

In [38]:
psdf = ps.DataFrame(df)

In [39]:
def add(data):
   return data[0] + data[1]

In [40]:
psdf.apply(add,axis=1)

/Users/ajinkyaparkar/anaconda3/lib/python3.10/site-packages/pyspark/pandas/utils.py:975: PandasAPIOnSparkAdviceWarning: If the type hints is not specified for `apply`, it is expensive to infer the data type internally.
  warnings.warn(message, PandasAPIOnSparkAdviceWarning)
23/06/13 23:07:42 WARN CSVHeaderChecker: Number of column in CSV header is not equal to number of fields in the schema:
 Header length: 79, schema size: 4
CSV file: file:///Users/ajinkyaparkar/Documents/leetcode/AWS/data/stackOverflow/survey_results_public.csv
23/06/13 23:07:43 WARN CSVHeaderChecker: Number of column in CSV header is not equal to number of fields in the schema:
 Header length: 79, schema size: 4
CSV file: file:///Users/ajinkyaparkar/Documents/leetcode/AWS/data/stackOverflow/survey_results_public.csv


0                                         1None of these
1                        2I am a developer by profession
2      3I am not primarily a developer, but I write c...
3                        4I am a developer by profession
4                        5I am a developer by profession
5      6I am not primarily a developer, but I write c...
6                           7I code primarily as a hobby
7                        8I am a developer by profession
8                        9I am a developer by profession
9                       10I am a developer by profession
10                      11I am a developer by profession
11     12I am not primarily a developer, but I write ...
12                      13I am a developer by profession
13                      14I am a developer by profession
14                      15I am a developer by profession
15                      16I am a developer by profession
16                      17I am a developer by profession
17                      18I am 

In [41]:
rdd = df.rdd

In [42]:
rdd2=rdd.map(lambda x: ((x[0],1),x[1],x[2],x[3]))
for element in rdd2.collect():
    print(element)

23/06/13 23:07:46 WARN CSVHeaderChecker: Number of column in CSV header is not equal to number of fields in the schema:
 Header length: 79, schema size: 4
CSV file: file:///Users/ajinkyaparkar/Documents/leetcode/AWS/data/stackOverflow/survey_results_public.csv
IOPub data rate exceeded.                                                       
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)




(('65720', 1), 'I am a developer by profession', 'Employed, full-time', 'Hybrid (some remote, some in-person)')
(('65721', 1), 'I used to be a developer by profession, but no longer am', 'Employed, full-time', 'Fully remote')
(('65722', 1), 'I am learning to code', 'Student, full-time', 'NA')
(('65723', 1), 'I am a developer by profession', 'Employed, full-time', 'Fully remote')
(('65724', 1), 'I am a developer by profession', 'Independent contractor, freelancer, or self-employed', 'Fully remote')
(('65725', 1), 'I am a developer by profession', 'Employed, full-time', 'Fully remote')
(('65726', 1), 'I am a developer by profession', 'Employed, full-time', 'Fully remote')
(('65727', 1), 'I am a developer by profession', 'Employed, full-time', 'Hybrid (some remote, some in-person)')
(('65728', 1), 'I am a developer by profession', 'Employed, full-time', 'Fully remote')
(('65729', 1), 'I am a developer by profession', 'Employed, full-time', 'Fully remote')
(('65730', 1), 'I am a developer

In [43]:
schema = StructType([
    StructField("mainBranch",StructType([
    StructField("field1", StringType(), nullable=False),
    StructField("field2", StringType(), nullable=False)
]),True),
     StructField("employment",StringType(),True),
     StructField("remoteWork",StringType(),True),
     StructField("codingActivities",StringType(),True)
])

In [44]:
rdd2.toDF(schema=schema).show()

+----------+--------------------+--------------------+--------------------+
|mainBranch|          employment|          remoteWork|    codingActivities|
+----------+--------------------+--------------------+--------------------+
|    {1, 1}|       None of these|                  NA|                  NA|
|    {2, 1}|I am a developer ...| Employed, full-time|        Fully remote|
|    {3, 1}|I am not primaril...| Employed, full-time|Hybrid (some remo...|
|    {4, 1}|I am a developer ...| Employed, full-time|        Fully remote|
|    {5, 1}|I am a developer ...| Employed, full-time|Hybrid (some remo...|
|    {6, 1}|I am not primaril...|  Student, full-time|                  NA|
|    {7, 1}|I code primarily ...|  Student, part-time|                  NA|
|    {8, 1}|I am a developer ...|Not employed, but...|                  NA|
|    {9, 1}|I am a developer ...| Employed, full-time|Hybrid (some remo...|
|   {10, 1}|I am a developer ...|Independent contr...|        Fully remote|
|   {11, 1}|

23/06/13 23:07:48 WARN CSVHeaderChecker: Number of column in CSV header is not equal to number of fields in the schema:
 Header length: 79, schema size: 4
CSV file: file:///Users/ajinkyaparkar/Documents/leetcode/AWS/data/stackOverflow/survey_results_public.csv


In [45]:
df1 = rdd2.toDF(schema=schema)

In [46]:
df1.show()

+----------+--------------------+--------------------+--------------------+
|mainBranch|          employment|          remoteWork|    codingActivities|
+----------+--------------------+--------------------+--------------------+
|    {1, 1}|       None of these|                  NA|                  NA|
|    {2, 1}|I am a developer ...| Employed, full-time|        Fully remote|
|    {3, 1}|I am not primaril...| Employed, full-time|Hybrid (some remo...|
|    {4, 1}|I am a developer ...| Employed, full-time|        Fully remote|
|    {5, 1}|I am a developer ...| Employed, full-time|Hybrid (some remo...|
|    {6, 1}|I am not primaril...|  Student, full-time|                  NA|
|    {7, 1}|I code primarily ...|  Student, part-time|                  NA|
|    {8, 1}|I am a developer ...|Not employed, but...|                  NA|
|    {9, 1}|I am a developer ...| Employed, full-time|Hybrid (some remo...|
|   {10, 1}|I am a developer ...|Independent contr...|        Fully remote|
|   {11, 1}|

23/06/13 23:07:48 WARN CSVHeaderChecker: Number of column in CSV header is not equal to number of fields in the schema:
 Header length: 79, schema size: 4
CSV file: file:///Users/ajinkyaparkar/Documents/leetcode/AWS/data/stackOverflow/survey_results_public.csv


In [47]:
rdd = df.rdd

In [48]:
rdd.collect()

23/06/13 23:07:48 WARN CSVHeaderChecker: Number of column in CSV header is not equal to number of fields in the schema:
 Header length: 79, schema size: 4
CSV file: file:///Users/ajinkyaparkar/Documents/leetcode/AWS/data/stackOverflow/survey_results_public.csv


[Row(mainBranch='1', employment='None of these', remoteWork='NA', codingActivities='NA'),
 Row(mainBranch='2', employment='I am a developer by profession', remoteWork='Employed, full-time', codingActivities='Fully remote'),
 Row(mainBranch='3', employment='I am not primarily a developer, but I write code sometimes as part of my work', remoteWork='Employed, full-time', codingActivities='Hybrid (some remote, some in-person)'),
 Row(mainBranch='4', employment='I am a developer by profession', remoteWork='Employed, full-time', codingActivities='Fully remote'),
 Row(mainBranch='5', employment='I am a developer by profession', remoteWork='Employed, full-time', codingActivities='Hybrid (some remote, some in-person)'),
 Row(mainBranch='6', employment='I am not primarily a developer, but I write code sometimes as part of my work', remoteWork='Student, full-time', codingActivities='NA'),
 Row(mainBranch='7', employment='I code primarily as a hobby', remoteWork='Student, part-time', codingActivit

In [49]:
rdd3 = rdd.flatMap(lambda x:(x[0],(x[1].split(" ")),x[2],x[3]))
rdd3.collect()

23/06/13 23:07:50 WARN CSVHeaderChecker: Number of column in CSV header is not equal to number of fields in the schema:
 Header length: 79, schema size: 4
CSV file: file:///Users/ajinkyaparkar/Documents/leetcode/AWS/data/stackOverflow/survey_results_public.csv


['1',
 ['None', 'of', 'these'],
 'NA',
 'NA',
 '2',
 ['I', 'am', 'a', 'developer', 'by', 'profession'],
 'Employed, full-time',
 'Fully remote',
 '3',
 ['I',
  'am',
  'not',
  'primarily',
  'a',
  'developer,',
  'but',
  'I',
  'write',
  'code',
  'sometimes',
  'as',
  'part',
  'of',
  'my',
  'work'],
 'Employed, full-time',
 'Hybrid (some remote, some in-person)',
 '4',
 ['I', 'am', 'a', 'developer', 'by', 'profession'],
 'Employed, full-time',
 'Fully remote',
 '5',
 ['I', 'am', 'a', 'developer', 'by', 'profession'],
 'Employed, full-time',
 'Hybrid (some remote, some in-person)',
 '6',
 ['I',
  'am',
  'not',
  'primarily',
  'a',
  'developer,',
  'but',
  'I',
  'write',
  'code',
  'sometimes',
  'as',
  'part',
  'of',
  'my',
  'work'],
 'Student, full-time',
 'NA',
 '7',
 ['I', 'code', 'primarily', 'as', 'a', 'hobby'],
 'Student, part-time',
 'NA',
 '8',
 ['I', 'am', 'a', 'developer', 'by', 'profession'],
 'Not employed, but looking for work',
 'NA',
 '9',
 ['I', 'am', 

In [51]:
for element in rdd3.collect():
    print(element)

23/06/13 23:08:24 WARN CSVHeaderChecker: Number of column in CSV header is not equal to number of fields in the schema:
 Header length: 79, schema size: 4
CSV file: file:///Users/ajinkyaparkar/Documents/leetcode/AWS/data/stackOverflow/survey_results_public.csv


1
['None', 'of', 'these']
NA
NA
2
['I', 'am', 'a', 'developer', 'by', 'profession']
Employed, full-time
Fully remote
3
['I', 'am', 'not', 'primarily', 'a', 'developer,', 'but', 'I', 'write', 'code', 'sometimes', 'as', 'part', 'of', 'my', 'work']
Employed, full-time
Hybrid (some remote, some in-person)
4
['I', 'am', 'a', 'developer', 'by', 'profession']
Employed, full-time
Fully remote
5
['I', 'am', 'a', 'developer', 'by', 'profession']
Employed, full-time
Hybrid (some remote, some in-person)
6
['I', 'am', 'not', 'primarily', 'a', 'developer,', 'but', 'I', 'write', 'code', 'sometimes', 'as', 'part', 'of', 'my', 'work']
Student, full-time
NA
7
['I', 'code', 'primarily', 'as', 'a', 'hobby']
Student, part-time
NA
8
['I', 'am', 'a', 'developer', 'by', 'profession']
Not employed, but looking for work
NA
9
['I', 'am', 'a', 'developer', 'by', 'profession']
Employed, full-time
Hybrid (some remote, some in-person)
10
['I', 'am', 'a', 'developer', 'by', 'profession']
Independent contractor, freel

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [52]:
df.show()

+----------+--------------------+--------------------+--------------------+
|mainBranch|          employment|          remoteWork|    codingActivities|
+----------+--------------------+--------------------+--------------------+
|         1|       None of these|                  NA|                  NA|
|         2|I am a developer ...| Employed, full-time|        Fully remote|
|         3|I am not primaril...| Employed, full-time|Hybrid (some remo...|
|         4|I am a developer ...| Employed, full-time|        Fully remote|
|         5|I am a developer ...| Employed, full-time|Hybrid (some remo...|
|         6|I am not primaril...|  Student, full-time|                  NA|
|         7|I code primarily ...|  Student, part-time|                  NA|
|         8|I am a developer ...|Not employed, but...|                  NA|
|         9|I am a developer ...| Employed, full-time|Hybrid (some remo...|
|        10|I am a developer ...|Independent contr...|        Fully remote|
|        11|

23/06/13 23:08:27 WARN CSVHeaderChecker: Number of column in CSV header is not equal to number of fields in the schema:
 Header length: 79, schema size: 4
CSV file: file:///Users/ajinkyaparkar/Documents/leetcode/AWS/data/stackOverflow/survey_results_public.csv


In [53]:
df.mainBranch

Column<'mainBranch'>

In [54]:
def f(df):
    print(df.mainBranch)
df.foreach(f)

23/06/13 23:08:30 WARN CSVHeaderChecker: Number of column in CSV header is not equal to number of fields in the schema:
 Header length: 79, schema size: 4
CSV file: file:///Users/ajinkyaparkar/Documents/leetcode/AWS/data/stackOverflow/survey_results_public.csv
56703
56704
56705
56706
56707
56708
56709
56710
56711
56712
56713
56714
56715
56716
56717
56718
56719
56720
56721
56722
56723
56724
56725
56726
56727
56728
56729
56730
56731
56732
56733
47308
47309
47310
47311
47312
47313
47314
47315
47316
47317
47318
47319
47320
47321
47322
47323
47324
47325
47326
47327
47328
47329
47330
47331
47332
47333
47334
47335
47336
47337
47338
47339
47340
47341
47342
47343
47344
47345
47346
47347
47348
47349
47350
47351
47352
47353
47354
47355
47356
47357
47358
47359
47360
47361
47362
47363
47364
47365
47366
47367
47368
47369
47370
47371
47372
47373
47374
47375
47376
47377
47378
47379
47380
47381
47382
47383
47384
47385
47386
47387
47388
47389
47390
47391
47392
47393
47394
47395
47396
47397
47398
47399
4

9613
9614
9615
9616
9617
9618
9619
9620
9621
9622
205
56830
56831
56832
56833
56834
56835
56836
56837
56838
56839
56840
56841
56842
56843
56844
56845
56846
56847
56848
56849
56850
56851
56852
56853
56854
56855
56856
56857
56858
56859
56860
56861
56862
56863
56864
206

207
208
209
210
211
19141
19142
19143
19144
19145
19146
19147
19148
19149
19150
19151
19152
19153
19154
19155
19156
19157
19158
19159
19160
19161
19162
191639623
9624
9625
9626
568659627
56866
56867
56868
56869
56870
56871
56872
56873
56874

56875
212
213
214
215
216
217
218
219
220
221
19164
19165
19166
19167
19168
19169
19170
19171
19172
19173
19174
19175
19176
19177
19178
19179
19180
19181
19182
19183
19184
19185
19186
19187
19188
19189
19190
19191
19192
19193
19194
19195
191969628
9629
9630
9631
9632
9633
9634
9635
9636
9637
9638
9639
9640
9641
9642
9643
9644
9645
9646



5687619197

964756877

56878
2225687919198
191999648

19200
19201
9649
19202
965019203

9651


56880965219204

223

5688119205


568829653
19206

22

6758039225

6758139226

6758239227

67583
39228
67584
39229
67585
39230
67586
39231
67587
39232
67588
39233
67589
39234
67590
39235
67591
39236
67592
39237
67593
39238
67594
39239
67595
39240
6759648692
39241

39242
6759739243
48693

39244
4869467598
67599
67600
67601
67602
67603
67604
67605
67606
67607
67608
67609
67610
67611
67612
67613
67614
67615
67616
67617
67618
67619
67620
67621
67622
67623
67624
67625
67626
67627
67628
67629
67630
39245
4869539246

39247
3924867631

3924967632

67633
4869667634

48697

48698
39250
67635
39251
6763639252

67637
48699
67638
48700
67639
48701
67640
48702
67641
48703
67642
48704
67643
48705
67644
48706
67645
48707
67646
48708
67647
3925367648

67649
67650
6765139254

67652
39255
67653
39256
6765439257

6765539258

6765639259
4870939260

3926148710

39262
48711
39263
48712
39264
48713
39265
48714
39266
48715
3926748716

3926848717


3926948718

3927048719

3927148720

3927248721

6765739273
48722
67658
48723
67659
48724
6766048725

48726
39274

3927

16422
6387245277
16423

1642463873

4527816425

63874
4527916426

45280

4528126125
45282

54802
45283
26126
5480345284
26127
638755480426128

164272612963876


2613063877

261316387816428

63879

63880
35700
63881
3570145285


2613245286
1642963882
45287
16430

4528816431

164322613345289

26134

26135
35702
26136
3570363883
26137

35704
2613863884
35705

26139
3570663885
26140

35707
261416388635708


54805

54806
1643354807
26142

1643426143

261446388716435
35709
63888

16436
6388935710

164376389035711


35712
16438
35713
45290
1643935714
45291

4529216440

452935480816441


54809
1644254810
26145

1644326146

2614716444


35715
26148
35716
2614963891
35717
26150

35718
26151
63892
26152

26153
45294

26154
45295
2615545296
164454529763893
54811

63894
54812
63895
3571954813
63896

54814
63897
54815
6389835720

54816
63899
5481735721
63900

54818
6390135722
54819

63902
548203572363903


2615616446

164474529826157


5482145299

5482235724

45300
5482335725

54824
6390454825


548

In [55]:
accum=spark.sparkContext.accumulator(1)
df.foreach(lambda x:accum.add(int(x.mainBranch)))
print(accum.value)

4313
3607645667

64314
3607745668

64315
3607845669

36079
45670

45671
552774567216833
265304567364316

45674

2653145675

64317
2653245676

64318
2653364319


2653464320

2653564321

36080
2653664322

36081
2653764323

26538


26539
55278
360826432455279
168342654064325

4567716835

26541
16836
26542
16837

26543
16838
26544
36083
26545

36084
26546
36085
2654755280

36086
2654855281

26549

4567826550
64326

26551
64327
26552
1683964328
26553

64329
2655416840
64330

2655516841
360875528216842

1684345679
55283


55284
45680
55285
2655655286
64331

16844
6433216845

456816433316846

6433416847
265576433536088

64336

2655864337

36089
2655964338

36090
2656064339

36091
2656136092


2656236093

26563

36094
26564
36095
5528736096


5528836097

5528936098
16848
5529064340
16849
456822656516850


45683

2656645684

2656745685

36099
2656845686

36100
2656945687

5529145688


45689
4569064341

168514569164342


4569264343

16852
4569364344

456943610164345
26570
64346

3610264347

2657

23/06/13 23:08:31 WARN CSVHeaderChecker: Number of column in CSV header is not equal to number of fields in the schema:
 Header length: 79, schema size: 4
CSV file: file:///Users/ajinkyaparkar/Documents/leetcode/AWS/data/stackOverflow/survey_results_public.csv


2684136547


In [56]:
df.show()

+----------+--------------------+--------------------+--------------------+
|mainBranch|          employment|          remoteWork|    codingActivities|
+----------+--------------------+--------------------+--------------------+
|         1|       None of these|                  NA|                  NA|
|         2|I am a developer ...| Employed, full-time|        Fully remote|
|         3|I am not primaril...| Employed, full-time|Hybrid (some remo...|
|         4|I am a developer ...| Employed, full-time|        Fully remote|
|         5|I am a developer ...| Employed, full-time|Hybrid (some remo...|
|         6|I am not primaril...|  Student, full-time|                  NA|
|         7|I code primarily ...|  Student, part-time|                  NA|
|         8|I am a developer ...|Not employed, but...|                  NA|
|         9|I am a developer ...| Employed, full-time|Hybrid (some remo...|
|        10|I am a developer ...|Independent contr...|        Fully remote|
|        11|

23/06/13 23:08:32 WARN CSVHeaderChecker: Number of column in CSV header is not equal to number of fields in the schema:
 Header length: 79, schema size: 4
CSV file: file:///Users/ajinkyaparkar/Documents/leetcode/AWS/data/stackOverflow/survey_results_public.csv


In [57]:
rdd4 = df.sample(1.0).collect()

23/06/13 23:08:32 WARN CSVHeaderChecker: Number of column in CSV header is not equal to number of fields in the schema:
 Header length: 79, schema size: 4
CSV file: file:///Users/ajinkyaparkar/Documents/leetcode/AWS/data/stackOverflow/survey_results_public.csv


In [58]:
len(rdd4)

73268

In [59]:
df.na.fill(value=0,subset=["remoteWork"]).limit(3).show()

+----------+--------------------+-------------------+--------------------+
|mainBranch|          employment|         remoteWork|    codingActivities|
+----------+--------------------+-------------------+--------------------+
|         1|       None of these|                 NA|                  NA|
|         2|I am a developer ...|Employed, full-time|        Fully remote|
|         3|I am not primaril...|Employed, full-time|Hybrid (some remo...|
+----------+--------------------+-------------------+--------------------+



23/06/13 23:08:33 WARN CSVHeaderChecker: Number of column in CSV header is not equal to number of fields in the schema:
 Header length: 79, schema size: 4
CSV file: file:///Users/ajinkyaparkar/Documents/leetcode/AWS/data/stackOverflow/survey_results_public.csv


In [60]:
df.withColumn("mainBranch",col("mainBranch").cast("Integer")).groupBy("employment").pivot("remoteWork").sum("mainBranch").show()



23/06/13 23:08:34 WARN CSVHeaderChecker: CSV header does not conform to the schema.
 Header: Employment
 Schema: remoteWork
Expected: remoteWork but found: Employment
CSV file: file:///Users/ajinkyaparkar/Documents/leetcode/AWS/data/stackOverflow/survey_results_public.csv
23/06/13 23:08:34 WARN package: Truncated the string representation of a plan since it was too large. This behavior can be adjusted by setting 'spark.sql.debug.maxToStringFields'.
23/06/13 23:08:35 WARN CSVHeaderChecker: CSV header does not conform to the schema.
 Header: ResponseId, MainBranch, Employment
 Schema: mainBranch, employment, remoteWork
Expected: mainBranch but found: ResponseId
CSV file: file:///Users/ajinkyaparkar/Documents/leetcode/AWS/data/stackOverflow/survey_results_public.csv


+--------------------+-------------------+---------------------------------------+------------------------------------------------------------------------+--------------------------------------------------------------------------------------------+-----------------------------------------------------------------------------------------------------------------------------------+---------------------------------------------------------------------------------------------------------------+--------------------------------------------------------------------------------+----------------------------------------------------------+------------------------------------------------------+--------------------------------------------------------------------------+-----------------------------------------------------------------------------------------------------------+-------------------------------------------------------------------------------------------------------------------------------+--

In [61]:
df.limit(5).write.option("header",True) \
        .partitionBy("employment") \
        .mode("overwrite") \
        .csv("/Users/ajinkyaparkar/Documents/leetcode/AWS/data/stackOverflow/output/")

23/06/13 23:08:36 WARN CSVHeaderChecker: Number of column in CSV header is not equal to number of fields in the schema:
 Header length: 79, schema size: 4
CSV file: file:///Users/ajinkyaparkar/Documents/leetcode/AWS/data/stackOverflow/survey_results_public.csv


In [62]:
df3=spark.read.option("header",True) \
                  .csv("/Users/ajinkyaparkar/Documents/leetcode/AWS/data/stackOverflow/output/")

In [63]:
df3.createOrReplaceTempView("datatable")
spark.sql("select * from datatable  where employment='None of these' and remoteWork = 'NA'") \
    .show()

+----------+----------+----------------+-------------+
|mainBranch|remoteWork|codingActivities|   employment|
+----------+----------+----------------+-------------+
|         1|        NA|              NA|None of these|
+----------+----------+----------------+-------------+



In [64]:
df3.show()

+----------+-------------------+--------------------+--------------------+
|mainBranch|         remoteWork|    codingActivities|          employment|
+----------+-------------------+--------------------+--------------------+
|         2|Employed, full-time|        Fully remote|I am a developer ...|
|         4|Employed, full-time|        Fully remote|I am a developer ...|
|         5|Employed, full-time|Hybrid (some remo...|I am a developer ...|
|         3|Employed, full-time|Hybrid (some remo...|I am not primaril...|
|         1|                 NA|                  NA|       None of these|
+----------+-------------------+--------------------+--------------------+



In [65]:
df.show()

+----------+--------------------+--------------------+--------------------+
|mainBranch|          employment|          remoteWork|    codingActivities|
+----------+--------------------+--------------------+--------------------+
|         1|       None of these|                  NA|                  NA|
|         2|I am a developer ...| Employed, full-time|        Fully remote|
|         3|I am not primaril...| Employed, full-time|Hybrid (some remo...|
|         4|I am a developer ...| Employed, full-time|        Fully remote|
|         5|I am a developer ...| Employed, full-time|Hybrid (some remo...|
|         6|I am not primaril...|  Student, full-time|                  NA|
|         7|I code primarily ...|  Student, part-time|                  NA|
|         8|I am a developer ...|Not employed, but...|                  NA|
|         9|I am a developer ...| Employed, full-time|Hybrid (some remo...|
|        10|I am a developer ...|Independent contr...|        Fully remote|
|        11|

23/06/13 23:08:37 WARN CSVHeaderChecker: Number of column in CSV header is not equal to number of fields in the schema:
 Header length: 79, schema size: 4
CSV file: file:///Users/ajinkyaparkar/Documents/leetcode/AWS/data/stackOverflow/survey_results_public.csv


In [66]:
states = {"NY":"New York", "CA":"California", "FL":"Florida"}
broadcastStates = spark.sparkContext.broadcast(states)
broadcastStates.value

{'NY': 'New York', 'CA': 'California', 'FL': 'Florida'}

In [67]:
type(broadcastStates)

pyspark.broadcast.Broadcast

In [68]:
"""
from pyspark.sql import SparkSession
from pyspark.streaming import StreamingContext

# Create a SparkSession
spark = SparkSession.builder.appName("StreamingExample").getOrCreate()

# Create a StreamingContext with batch interval of 1 second
ssc = StreamingContext(spark.sparkContext, 1)

# Define the input source (in this case, a directory)
inputDirectory = "/Users/ajinkyaparkar/Documents/leetcode/AWS/data/stackOverflow/output/"

# Create a DStream by monitoring the input directory
lines = ssc.textFileStream(inputDirectory)

# Perform transformations on the DStream (word count example)
wordCounts = lines.flatMap(lambda line: line.split(" ")) \
                  .map(lambda word: (word, 1)) \
                  .reduceByKey(lambda a, b: a + b)

# Print the word counts to the console
wordCounts.pprint()

# Start the streaming context
ssc.start()

# Wait for the streaming to
finish (or manually stop it)
ssc.awaitTermination()
"""

'\nfrom pyspark.sql import SparkSession\nfrom pyspark.streaming import StreamingContext\n\n# Create a SparkSession\nspark = SparkSession.builder.appName("StreamingExample").getOrCreate()\n\n# Create a StreamingContext with batch interval of 1 second\nssc = StreamingContext(spark.sparkContext, 1)\n\n# Define the input source (in this case, a directory)\ninputDirectory = "/Users/ajinkyaparkar/Documents/leetcode/AWS/data/stackOverflow/output/"\n\n# Create a DStream by monitoring the input directory\nlines = ssc.textFileStream(inputDirectory)\n\n# Perform transformations on the DStream (word count example)\nwordCounts = lines.flatMap(lambda line: line.split(" "))                   .map(lambda word: (word, 1))                   .reduceByKey(lambda a, b: a + b)\n\n# Print the word counts to the console\nwordCounts.pprint()\n\n# Start the streaming context\nssc.start()\n\n# Wait for the streaming to\nfinish (or manually stop it)\nssc.awaitTermination()\n'

In [69]:
"""
from pyspark.sql import SparkSession

# Create a SparkSession
spark = SparkSession.builder \
    .appName("KafkaStreamingExample") \
    .getOrCreate()

# Configure Kafka integration
spark.conf.set("spark.sql.streaming.checkpointLocation", "/path/to/checkpoint/location")
spark.conf.set("spark.sql.shuffle.partitions", "10")  # Set the desired number of shuffle partitions

# Define the Kafka parameters
kafkaParams = {
    "kafka.bootstrap.servers": "localhost:9092",  # Kafka broker address
    "subscribe": "Context-kafka"  # Kafka topic to subscribe to
}

# Read data from Kafka using the Kafka source
df = spark.readStream.format("kafka") \
    .options(**kafkaParams) \
    .load()

# Perform further operations on the streaming DataFrame
# For example, you can extract the key and value columns
df = df.selectExpr("CAST(key AS STRING)", "CAST(value AS STRING)")

# Start the streaming query
query = df.writeStream \
    .outputMode("append") \
    .format("console") \
    .start()

# Wait for the streaming to finishfrom pyspark.sql import SparkSession

# Create a SparkSession
spark = SparkSession.builder \
    .appName("KafkaStreamingExample") \
    .getOrCreate()

# Configure Kafka integration
spark.conf.set("spark.sql.streaming.checkpointLocation", "/path/to/checkpoint/location")
spark.conf.set("spark.sql.shuffle.partitions", "10")  # Set the desired number of shuffle partitions

# Define the Kafka parameters
kafkaParams = {
    "kafka.bootstrap.servers": "localhost:9092",  # Kafka broker address
    "subscribe": "Context-kafka"  # Kafka topic to subscribe to
}

# Read data from Kafka using the Kafka source
df = spark.readStream.format("kafka") \
    .options(**kafkaParams) \
    .load()

# Perform further operations on the streaming DataFrame
# For example, you can extract the key and value columns
df = df.selectExpr("CAST(key AS STRING)", "CAST(value AS STRING)")

# Start the streaming query
query = df.writeStream \
    .outputMode("append") \
    .format("console") \
    .start()

# Wait for the streaming to finish (or manually stop it)
query.awaitTermination()
 (or manually stop it)
query.awaitTermination()
In this example, we create a SparkSession with the application name "KafkaStreamingExample". We set the necessary configuration properties for Kafka integration using spark.conf.set(). The spark.sql.streaming.checkpointLocation specifies the checkpoint directory where the streaming query metadata will be stored, and spark.sql.shuffle.partitions determines the number of shuffle partitions.

Next, we define the Kafka parameters as a dictionary (kafkaParams), including the Kafka bootstrap servers and the topic to subscribe to.

We use the readStream method to create a streaming DataFrame from Kafka by specifying the format as "kafka" and providing the Kafka parameters. Further operations can be performed on the streaming DataFrame, such as selecting specific columns or applying transformations.

Finally, we start the streaming query by invoking the writeStream method. In this example, we write the streaming data to the console using format("console"). You can replace it with other output sinks like Kafka, HDFS, or a database. The outputMode is set to "append", which means only new rows will be written to the output.

Lastly, we call awaitTermination() to wait for the streaming query to finish. You can manually stop the streaming query by calling the stop() method on the query object.

Make sure to adjust the Kafka broker address, topic, checkpoint location, and other configuration parameters based on your specific Kafka setup and requirements.

I hope this example helps you get started with Kafka streaming using SparkSession in PySpark. Let me know if you have any further questions!

"""







'\nfrom pyspark.sql import SparkSession\n\n# Create a SparkSession\nspark = SparkSession.builder     .appName("KafkaStreamingExample")     .getOrCreate()\n\n# Configure Kafka integration\nspark.conf.set("spark.sql.streaming.checkpointLocation", "/path/to/checkpoint/location")\nspark.conf.set("spark.sql.shuffle.partitions", "10")  # Set the desired number of shuffle partitions\n\n# Define the Kafka parameters\nkafkaParams = {\n    "kafka.bootstrap.servers": "localhost:9092",  # Kafka broker address\n    "subscribe": "Context-kafka"  # Kafka topic to subscribe to\n}\n\n# Read data from Kafka using the Kafka source\ndf = spark.readStream.format("kafka")     .options(**kafkaParams)     .load()\n\n# Perform further operations on the streaming DataFrame\n# For example, you can extract the key and value columns\ndf = df.selectExpr("CAST(key AS STRING)", "CAST(value AS STRING)")\n\n# Start the streaming query\nquery = df.writeStream     .outputMode("append")     .format("console")     .start()

In [70]:
rdd1 = spark.sparkContext.parallelize(range(0,25), 20)


In [71]:
print("From local[100] : "+str(rdd1.getNumPartitions()))

From local[100] : 20


In [72]:
schema = StructType([
    StructField("id",IntegerType(),True),
    StructField("name",StringType(),True),
    ])

In [73]:
# Create DataFrame 1
df8 = spark.createDataFrame([(1, "Alice"), (2, "Bob"), (3, "Charlie")], ["id", "name"],schema)

# Create DataFrame 2 (small DataFrame)
df9 = spark.createDataFrame([(1, "USA"), (2, "Canada"), (3, "UK")], ["id", "country"],schema)

# Broadcast the small DataFrame
broadcast_df2 = broadcast(df9)

In [112]:
joined_df = df8.join(broadcast_df2, on="id", how="inner")
joined_df.show()

ConnectionRefusedError: [Errno 61] Connection refused

In [75]:
data = [("Banana",1000,"USA","yellow",["a","b","c"]), ("Carrots",1500,"USA","orange",["a,b,c"]), ("Beans",1600,"USA","brown",["a,b,c"]), \
      ("Orange",2000,"USA","orange",["a","b","c"]),("Orange",2000,"USA","orange",["a,b,c"]),("Banana",400,"China","yellow",["a,b,c"]), \
      ("Carrots",1200,"China","orange",["a","b","c"]),("Beans",1500,"China","brown",["a,b,c"]),("Orange",4000,"China","orange",["a,b,c"]), \
      ("Banana",2000,"Canada","yellow",["a","b","c"]),("Carrots",2000,"Canada","orange",["a,b,c"]),("Beans",2000,"Mexico","brown",["a,b,c"])]

columns= ["Product","Amount","Country","color","chars"]
dframe = spark.createDataFrame(data = data, schema = columns)
dframe.printSchema()

root
 |-- Product: string (nullable = true)
 |-- Amount: long (nullable = true)
 |-- Country: string (nullable = true)
 |-- color: string (nullable = true)
 |-- chars: array (nullable = true)
 |    |-- element: string (containsNull = true)



In [76]:
dframe.groupby("Product").pivot("Country").avg("Amount").show()

+-------+------+------+------+------+
|Product|Canada| China|Mexico|   USA|
+-------+------+------+------+------+
| Orange|  null|4000.0|  null|2000.0|
|  Beans|  null|1500.0|2000.0|1600.0|
| Banana|2000.0| 400.0|  null|1000.0|
|Carrots|2000.0|1200.0|  null|1500.0|
+-------+------+------+------+------+



In [77]:
dfexplode = dframe.select(col("*"),explode(col("chars"))).show()

+-------+------+-------+------+---------+-----+
|Product|Amount|Country| color|    chars|  col|
+-------+------+-------+------+---------+-----+
| Banana|  1000|    USA|yellow|[a, b, c]|    a|
| Banana|  1000|    USA|yellow|[a, b, c]|    b|
| Banana|  1000|    USA|yellow|[a, b, c]|    c|
|Carrots|  1500|    USA|orange|  [a,b,c]|a,b,c|
|  Beans|  1600|    USA| brown|  [a,b,c]|a,b,c|
| Orange|  2000|    USA|orange|[a, b, c]|    a|
| Orange|  2000|    USA|orange|[a, b, c]|    b|
| Orange|  2000|    USA|orange|[a, b, c]|    c|
| Orange|  2000|    USA|orange|  [a,b,c]|a,b,c|
| Banana|   400|  China|yellow|  [a,b,c]|a,b,c|
|Carrots|  1200|  China|orange|[a, b, c]|    a|
|Carrots|  1200|  China|orange|[a, b, c]|    b|
|Carrots|  1200|  China|orange|[a, b, c]|    c|
|  Beans|  1500|  China| brown|  [a,b,c]|a,b,c|
| Orange|  4000|  China|orange|  [a,b,c]|a,b,c|
| Banana|  2000| Canada|yellow|[a, b, c]|    a|
| Banana|  2000| Canada|yellow|[a, b, c]|    b|
| Banana|  2000| Canada|yellow|[a, b, c]

# Explode

In [78]:
import pyspark
from pyspark.sql import SparkSession

spark = SparkSession.builder.appName('pyspark-by-examples').getOrCreate()

arrayArrayData = [
  ("James","2",["Java","Spark"]),
  ("Michael","2",["C++","Java"]),
  ("Robert","2",["CSharp","Python"])
]

df_explode = spark.createDataFrame(data=arrayArrayData, schema = ['name','age','subjects'])
df_explode.printSchema()
df_explode.show(truncate=False)

root
 |-- name: string (nullable = true)
 |-- age: string (nullable = true)
 |-- subjects: array (nullable = true)
 |    |-- element: string (containsNull = true)



23/06/13 23:08:40 WARN SparkSession: Using an existing Spark session; only runtime SQL configurations will take effect.


+-------+---+----------------+
|name   |age|subjects        |
+-------+---+----------------+
|James  |2  |[Java, Spark]   |
|Michael|2  |[C++, Java]     |
|Robert |2  |[CSharp, Python]|
+-------+---+----------------+



In [79]:
df_explode.select(col("*"),explode("subjects")).show(truncate=False)

+-------+---+----------------+------+
|name   |age|subjects        |col   |
+-------+---+----------------+------+
|James  |2  |[Java, Spark]   |Java  |
|James  |2  |[Java, Spark]   |Spark |
|Michael|2  |[C++, Java]     |C++   |
|Michael|2  |[C++, Java]     |Java  |
|Robert |2  |[CSharp, Python]|CSharp|
|Robert |2  |[CSharp, Python]|Python|
+-------+---+----------------+------+



In [80]:
pivotDF = dframe.groupBy("Product","chars").pivot("Country").sum("Amount")
pivotDF.printSchema()
pivotDF.show(truncate=False)

root
 |-- Product: string (nullable = true)
 |-- chars: array (nullable = true)
 |    |-- element: string (containsNull = true)
 |-- Canada: long (nullable = true)
 |-- China: long (nullable = true)
 |-- Mexico: long (nullable = true)
 |-- USA: long (nullable = true)

+-------+---------+------+-----+------+----+
|Product|chars    |Canada|China|Mexico|USA |
+-------+---------+------+-----+------+----+
|Banana |[a, b, c]|2000  |null |null  |1000|
|Orange |[a, b, c]|null  |null |null  |2000|
|Carrots|[a, b, c]|null  |1200 |null  |null|
|Orange |[a,b,c]  |null  |4000 |null  |2000|
|Beans  |[a,b,c]  |null  |1500 |2000  |1600|
|Banana |[a,b,c]  |null  |400  |null  |null|
|Carrots|[a,b,c]  |2000  |null |null  |1500|
+-------+---------+------+-----+------+----+



In [81]:
pivotDF = pivotDF.select(col("*"),explode("chars"))
pivotDF.show()

+-------+---------+------+-----+------+----+-----+
|Product|    chars|Canada|China|Mexico| USA|  col|
+-------+---------+------+-----+------+----+-----+
| Banana|[a, b, c]|  2000| null|  null|1000|    a|
| Banana|[a, b, c]|  2000| null|  null|1000|    b|
| Banana|[a, b, c]|  2000| null|  null|1000|    c|
| Orange|[a, b, c]|  null| null|  null|2000|    a|
| Orange|[a, b, c]|  null| null|  null|2000|    b|
| Orange|[a, b, c]|  null| null|  null|2000|    c|
|Carrots|[a, b, c]|  null| 1200|  null|null|    a|
|Carrots|[a, b, c]|  null| 1200|  null|null|    b|
|Carrots|[a, b, c]|  null| 1200|  null|null|    c|
| Orange|  [a,b,c]|  null| 4000|  null|2000|a,b,c|
|  Beans|  [a,b,c]|  null| 1500|  2000|1600|a,b,c|
| Banana|  [a,b,c]|  null|  400|  null|null|a,b,c|
|Carrots|  [a,b,c]|  2000| null|  null|1500|a,b,c|
+-------+---------+------+-----+------+----+-----+



In [82]:
pivotDF.persist()

DataFrame[Product: string, chars: array<string>, Canada: bigint, China: bigint, Mexico: bigint, USA: bigint, col: string]

In [83]:
pivotDF.dropna().show()

+-------+-----+------+-----+------+---+---+
|Product|chars|Canada|China|Mexico|USA|col|
+-------+-----+------+-----+------+---+---+
+-------+-----+------+-----+------+---+---+



In [84]:
spark = SparkSession.builder.getOrCreate()

# Create a sample DataFrame
data = [
    ("Alice", "Apple,Orange"),
    ("Bob", "Banana"),
    ("Charlie", "Grape,Mango,Cherry"),
]

df_split = spark.createDataFrame(data, ["Name", "Fruits"])
df_split.show()



+-------+------------------+
|   Name|            Fruits|
+-------+------------------+
|  Alice|      Apple,Orange|
|    Bob|            Banana|
|Charlie|Grape,Mango,Cherry|
+-------+------------------+



In [85]:
df_split.printSchema()
df_split.show()

root
 |-- Name: string (nullable = true)
 |-- Fruits: string (nullable = true)

+-------+------------------+
|   Name|            Fruits|
+-------+------------------+
|  Alice|      Apple,Orange|
|    Bob|            Banana|
|Charlie|Grape,Mango,Cherry|
+-------+------------------+



In [86]:
df_split = df_split.withColumn("split",split(col("Fruits"),","))
df_split.show()

+-------+------------------+--------------------+
|   Name|            Fruits|               split|
+-------+------------------+--------------------+
|  Alice|      Apple,Orange|     [Apple, Orange]|
|    Bob|            Banana|            [Banana]|
|Charlie|Grape,Mango,Cherry|[Grape, Mango, Ch...|
+-------+------------------+--------------------+



In [87]:
df_split.withColumn("Fruit", explode(split(col("Fruits"), ","))).show()

+-------+------------------+--------------------+------+
|   Name|            Fruits|               split| Fruit|
+-------+------------------+--------------------+------+
|  Alice|      Apple,Orange|     [Apple, Orange]| Apple|
|  Alice|      Apple,Orange|     [Apple, Orange]|Orange|
|    Bob|            Banana|            [Banana]|Banana|
|Charlie|Grape,Mango,Cherry|[Grape, Mango, Ch...| Grape|
|Charlie|Grape,Mango,Cherry|[Grape, Mango, Ch...| Mango|
|Charlie|Grape,Mango,Cherry|[Grape, Mango, Ch...|Cherry|
+-------+------------------+--------------------+------+



In [88]:
# Explode comma-separated strings
exploded_df = df_split.withColumn("Fruit", explode(split(col("Fruits"), ",")))
exploded_df.show()

+-------+------------------+--------------------+------+
|   Name|            Fruits|               split| Fruit|
+-------+------------------+--------------------+------+
|  Alice|      Apple,Orange|     [Apple, Orange]| Apple|
|  Alice|      Apple,Orange|     [Apple, Orange]|Orange|
|    Bob|            Banana|            [Banana]|Banana|
|Charlie|Grape,Mango,Cherry|[Grape, Mango, Ch...| Grape|
|Charlie|Grape,Mango,Cherry|[Grape, Mango, Ch...| Mango|
|Charlie|Grape,Mango,Cherry|[Grape, Mango, Ch...|Cherry|
+-------+------------------+--------------------+------+



In [89]:
df_split.printSchema()

root
 |-- Name: string (nullable = true)
 |-- Fruits: string (nullable = true)
 |-- split: array (nullable = true)
 |    |-- element: string (containsNull = false)



In [90]:
df_split.show()

+-------+------------------+--------------------+
|   Name|            Fruits|               split|
+-------+------------------+--------------------+
|  Alice|      Apple,Orange|     [Apple, Orange]|
|    Bob|            Banana|            [Banana]|
|Charlie|Grape,Mango,Cherry|[Grape, Mango, Ch...|
+-------+------------------+--------------------+



In [91]:
from pyspark.sql.functions import expr
data=[("2019-01-23",1),("2019-06-24",2),("2019-09-20",3),("2019-09-20",None)] 
df_date=spark.createDataFrame(data).toDF("date","increment") 

#Add Month value from another column
df_date.select(df_date.date,df_date.increment,
     expr("add_months(date,increment)")
  .alias("inc_date")).show()

+----------+---------+----------+
|      date|increment|  inc_date|
+----------+---------+----------+
|2019-01-23|        1|2019-02-23|
|2019-06-24|        2|2019-08-24|
|2019-09-20|        3|2019-12-20|
|2019-09-20|     null|      null|
+----------+---------+----------+



In [92]:
df_date.withColumn("testExp",expr("increment +5 as new_increment")).show()

+----------+---------+-------+
|      date|increment|testExp|
+----------+---------+-------+
|2019-01-23|        1|      6|
|2019-06-24|        2|      7|
|2019-09-20|        3|      8|
|2019-09-20|     null|   null|
+----------+---------+-------+



In [93]:
df_date.na.fill(0).show()

+----------+---------+
|      date|increment|
+----------+---------+
|2019-01-23|        1|
|2019-06-24|        2|
|2019-09-20|        3|
|2019-09-20|        0|
+----------+---------+



In [94]:
a = df_date.na.drop()
a.show()

+----------+---------+
|      date|increment|
+----------+---------+
|2019-01-23|        1|
|2019-06-24|        2|
|2019-09-20|        3|
+----------+---------+



In [95]:
exploded_df.groupBy("Name").agg(count("Name").alias("count")).orderBy(desc("count")).show()

+-------+-----+
|   Name|count|
+-------+-----+
|Charlie|    3|
|  Alice|    2|
|    Bob|    1|
+-------+-----+



In [96]:
def upper(s):
    return s.upper()
rdd.map(lambda p: (upper(p[1]))).collect()

23/06/13 23:08:48 WARN CSVHeaderChecker: Number of column in CSV header is not equal to number of fields in the schema:
 Header length: 79, schema size: 4
CSV file: file:///Users/ajinkyaparkar/Documents/leetcode/AWS/data/stackOverflow/survey_results_public.csv


['NONE OF THESE',
 'I AM A DEVELOPER BY PROFESSION',
 'I AM NOT PRIMARILY A DEVELOPER, BUT I WRITE CODE SOMETIMES AS PART OF MY WORK',
 'I AM A DEVELOPER BY PROFESSION',
 'I AM A DEVELOPER BY PROFESSION',
 'I AM NOT PRIMARILY A DEVELOPER, BUT I WRITE CODE SOMETIMES AS PART OF MY WORK',
 'I CODE PRIMARILY AS A HOBBY',
 'I AM A DEVELOPER BY PROFESSION',
 'I AM A DEVELOPER BY PROFESSION',
 'I AM A DEVELOPER BY PROFESSION',
 'I AM A DEVELOPER BY PROFESSION',
 'I AM NOT PRIMARILY A DEVELOPER, BUT I WRITE CODE SOMETIMES AS PART OF MY WORK',
 'I AM A DEVELOPER BY PROFESSION',
 'I AM A DEVELOPER BY PROFESSION',
 'I AM A DEVELOPER BY PROFESSION',
 'I AM A DEVELOPER BY PROFESSION',
 'I AM A DEVELOPER BY PROFESSION',
 'I AM A DEVELOPER BY PROFESSION',
 'I AM A DEVELOPER BY PROFESSION',
 'I AM LEARNING TO CODE',
 'I AM A DEVELOPER BY PROFESSION',
 'I AM A DEVELOPER BY PROFESSION',
 'I AM A DEVELOPER BY PROFESSION',
 'I AM NOT PRIMARILY A DEVELOPER, BUT I WRITE CODE SOMETIMES AS PART OF MY WORK',
 

# Map

In [101]:
df.show()

+----------+--------------------+--------------------+--------------------+
|mainBranch|          employment|          remoteWork|    codingActivities|
+----------+--------------------+--------------------+--------------------+
|         1|       None of these|                  NA|                  NA|
|         2|I am a developer ...| Employed, full-time|        Fully remote|
|         3|I am not primaril...| Employed, full-time|Hybrid (some remo...|
|         4|I am a developer ...| Employed, full-time|        Fully remote|
|         5|I am a developer ...| Employed, full-time|Hybrid (some remo...|
|         6|I am not primaril...|  Student, full-time|                  NA|
|         7|I code primarily ...|  Student, part-time|                  NA|
|         8|I am a developer ...|Not employed, but...|                  NA|
|         9|I am a developer ...| Employed, full-time|Hybrid (some remo...|
|        10|I am a developer ...|Independent contr...|        Fully remote|
|        11|

23/06/13 23:10:00 WARN CSVHeaderChecker: Number of column in CSV header is not equal to number of fields in the schema:
 Header length: 79, schema size: 4
CSV file: file:///Users/ajinkyaparkar/Documents/leetcode/AWS/data/stackOverflow/survey_results_public.csv


In [109]:
df2 = df.withColumn("test", when(df.employment == "None of these",df.remoteWork).otherwise(df.employment))

In [110]:
df2.show()

+----------+--------------------+--------------------+--------------------+--------------------+
|mainBranch|          employment|          remoteWork|    codingActivities|                test|
+----------+--------------------+--------------------+--------------------+--------------------+
|         1|       None of these|                  NA|                  NA|                  NA|
|         2|I am a developer ...| Employed, full-time|        Fully remote|I am a developer ...|
|         3|I am not primaril...| Employed, full-time|Hybrid (some remo...|I am not primaril...|
|         4|I am a developer ...| Employed, full-time|        Fully remote|I am a developer ...|
|         5|I am a developer ...| Employed, full-time|Hybrid (some remo...|I am a developer ...|
|         6|I am not primaril...|  Student, full-time|                  NA|I am not primaril...|
|         7|I code primarily ...|  Student, part-time|                  NA|I code primarily ...|
|         8|I am a developer .

23/06/13 23:13:53 WARN CSVHeaderChecker: Number of column in CSV header is not equal to number of fields in the schema:
 Header length: 79, schema size: 4
CSV file: file:///Users/ajinkyaparkar/Documents/leetcode/AWS/data/stackOverflow/survey_results_public.csv
